In [1]:
pip install pyspark

Note: you may need to restart the kernel to use updated packages.


In [5]:
from pyspark.sql import SparkSession
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number, when, col
from pyspark.sql.functions import count as _count
from pyspark.sql.functions import min as _min
from datetime import datetime
import psutil
import multiprocessing
import findspark


In [6]:
total_memory = psutil.virtual_memory().total / (1024**3)
memory_alocated = round(total_memory / 2)
num_cores = multiprocessing.cpu_count()
print(f'{total_memory} disponível. {memory_alocated} será alocada nesse processo. {num_cores} núcleos do processador serão envolvidos no processo')
spark = ""

findspark.init()
spark = SparkSession.builder.master("local[*]") \
    .appName("source_archive") \
    .config("spark.executor.memory", f"{memory_alocated}g") \
    .config("spark.executor.instances", f"{num_cores}") \
    .getOrCreate()

7.778934478759766 disponível. 4 será alocada nesse processo. 8 núcleos do processador serão envolvidos no processo


In [13]:
import os
import csv
import pandas as pd
import chardet

root_path = r'C:\Users\Guilherme\Documents\Talent Pool\Tropa BI\HDI\Arquivos_fornecedores-Reprocessamento'

csv_files = []

parquet_files = []

data = []

total_columns = 0

providers = ['Agger', 'Infocap', 'Quiver', 'Segfy']

columns = ['Provider', 'ArchiveName', 'Headers', 'Cols','CountColumns']

def valid_names(provider, sep):
    for folder in os.listdir(root_path):
    # Para cada diretório no caminho 'root_path'
        if folder.startswith(provider):
        # Se iníco do nome da pasta corresponder com os nomes da lista 'providers'  
            files_list = os.listdir(os.path.join(root_path, folder))
            # file_list será a junção do caminho 'root_path' com a o nome da pasta 'folder'
            for file in files_list:
            # Para cada arquivo na lista 'files_list'
                if file.endswith('.csv'):
                # Se o arquivo começa com '.csv'
                    csv_path = os.path.join(root_path, folder, file)
                    # 'csv_path' será a junção do caminho 'root_path', da pasta 'folder', e do arquivo 'file'.
                    print(f'Caminho: {csv_path} \n')
                    df = spark.read.csv(csv_path, sep=sep, encoding='utf-8', header=True)
                    # Lê o arquivo CSV usando Spark e especifica o separador e a codificação
                    headers = df.columns
                    # Obtém os nomes das colunas do DataFrame e armazena em 'headers'
                    cols = []
                     # Cria uma lista vazia para armazenar os nomes das colunas
                    for col in headers:
                      cols.append(col)
                      # Adiciona o nome da coluna à lista 'cols'
                    print(f'Colunas separadas: {cols} \n')
                    header_count = len(df.columns)
                    # Calcula o número de colunas do DataFrame.
                    print(f'Quantidade de colunas: {header_count} \n')


                elif file.endswith('.parquet'):
                # Se o arquivo começa com '.parquet'
                    parquet_path = os.path.join(root_path, folder, file)
                    # 'parquet_path' será a junção do caminho 'root_path', da pasta 'folder', e do arquivo 'file'.
                    print(f'Caminho: {parquet_path} \n')
                    df = spark.read.parquet(parquet_path)
                    # Lê o arquivo PARQUET usando Spark e especifica o separador e a codificação
                    headers = df.columns
                    # Obtém os nomes das colunas do DataFrame e armazena em 'headers'
                    cols = []
                     # Cria uma lista vazia para armazenar os nomes das colunas
                    for col in headers:
                      cols.append(col)
                      # Adiciona o nome da coluna à lista 'cols'
                    print(f'Colunas separadas: {cols} \n')
                    header_count = len(df.columns)
                    # Calcula o número de colunas do DataFrame.
                    print(f'Quantidade de colunas: {header_count} \n')

                data.append([provider, file, headers, cols, header_count])
                # A lista 'data' receberá as variáveis 	'provider', 'file', 'headers', 'cols', 'header_count'
                print(data)
                print()
df = pd.DataFrame(data, columns=columns)
# Cria um DataFrame utilizando os dados da lista 'data' e os nomes das colunas da lista 'columns'


df

Empty DataFrame
Columns: [Provider, ArchiveName, Headers, Cols, CountColumns]
Index: []

In [14]:
valid_names('TEX',',')

Caminho: C:\Users\Guilherme\Documents\Talent Pool\Tropa BI\HDI\Arquivos_fornecedores-Reprocessamento\TEX\Analytics_HDI_20211227-20220102_65.csv 

Colunas separadas: ['Key', 'Seguradora_NumeroCalculo', 'Ranking', 'Seguradora', 'Cluster', 'TipoSeguro', 'Risco_DataCalculo', 'Risco_InicioVigencia', 'Risco_FimVigenciaAnterior', 'Risco_Cobertura', 'Risco_CalculoPerfil', 'Risco_TipoFranquia', 'Coberturas_ISDM', 'Coberturas_ISDC', 'Coberturas_ISDMO', 'Coberturas_APPMo', 'Coberturas_APPInv', 'Coberturas_DE', 'Coberturas_Vidros', 'Coberturas_17a25Anos', 'Coberturas_Assistencia', 'Coberturas_CarroReserva', 'Assistencias_KM', 'Carro_reserva_Dias', '% Fipe', 'Segurado_Sexo', 'Segurado_TipoPessoa', 'Segurado_EstadoCivil', 'Segurado_DataNascimento', 'Condutor_Sexo', 'Condutor_EstadoCivil', 'Condutor_DataNascimento', 'Condutor_RelacaoSegurado', 'Veiculo_CodigoFipe', 'Veiculo_AnoModelo', 'Veiculo_ZeroKM', 'Veiculo_PercentualFipe', 'Veiculo_TipoValor', 'Veiculo_Passageiros', 'Historico_ClasseBonusAtual'

In [15]:
df = pd.DataFrame(data, columns=columns)


df

Provider                             ArchiveName  \
0       TEX  Analytics_HDI_20211227-20220102_65.csv   
1       TEX  Analytics_HDI_20220103-20220109_65.csv   
2       TEX  Analytics_HDI_20220110-20220116_65.csv   
3       TEX  Analytics_HDI_20220117-20220123_65.csv   
4       TEX  Analytics_HDI_20220124-20220130_65.csv   
..      ...                                     ...   
75      TEX           Analytics_HDI_20221225_65.csv   
76      TEX           Analytics_HDI_20221226_65.csv   
77      TEX           Analytics_HDI_20221227_65.csv   
78      TEX           Analytics_HDI_20221228_65.csv   
79      TEX           Analytics_HDI_20221229_65.csv   

                                              Headers  \
0   [Key, Seguradora_NumeroCalculo, Ranking, Segur...   
1   [Key, Seguradora_NumeroCalculo, Ranking, Segur...   
2   [Key, Seguradora_NumeroCalculo, Ranking, Segur...   
3   [Key, Seguradora_NumeroCalculo, Ranking, Segur...   
4   [Key, Seguradora_NumeroCalculo, Ranking, Segur...   
..                                                ...   
75  [Key, Seguradora_NumeroCalculo, Ranking, Segur...   
76  [Key, Seguradora_NumeroCalculo, Ranking, Segur...   
77  [Key, Seguradora_NumeroCalculo, Ranking, Segur...   
78  [Key, Seguradora_NumeroCalculo, Ranking, Segur...   
79  [Key, Seguradora_NumeroCalculo, Ranking, Segur...   

                                                 Cols  CountColumns  
0   [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  
1   [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  
2   [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  
3   [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  
4   [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  
..                                                ...           ...  
75  [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  
76  [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  
77  [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  
78  [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  
79  [Key, Seguradora_NumeroCalculo, Ranking, Segur...            65  

[80 rows x 5 columns]

In [17]:
df.to_csv(r'C:\Users\Guilherme\Documents\Talent Pool\Tropa BI\HDI\Multicalculo_validação' + df['Provider'][0] + '.csv', index=False)

In [19]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 80 entries, 0 to 79
Data columns (total 5 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   Provider      80 non-null     object
 1   ArchiveName   80 non-null     object
 2   Headers       80 non-null     object
 3   Cols          80 non-null     object
 4   CountColumns  80 non-null     int64 
dtypes: int64(1), object(4)
memory usage: 3.2+ KB


In [22]:
df.dtypes

Provider        object
ArchiveName     object
Headers         object
Cols            object
CountColumns     int64
dtype: object